In [5]:
import pandas as pd
from datetime import datetime, date, timedelta
import os
import glob
from difflib import get_close_matches
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
import numpy as np
import re
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
from scipy.sparse import csr_matrix
import time
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import sparse_dot_topn.sparse_dot_topn as ct

In [6]:
stock_industries_file = os.path.join("output\sp500\industries", "sp500_industries.csv")
df_industries = pd.read_csv(stock_industries_file)
#df_industries.head(20)
sp500_names=df_industries.loc[:,["ticker", "longName"]]

In [7]:
unofficial_name=[]

for name in sp500_names["longName"]:
    x=name.rstrip("Inc.").rstrip("plc").rstrip("Incorporated").rstrip("Corporatio").strip().rstrip(",")
    unofficial_name.append(x)

sp500_names["unofficial_name"]= unofficial_name

In [8]:
sp500_names.head(20)

ticker                                     longName  \
0       A                   Agilent Technologies, Inc.   
1     AAL                 American Airlines Group Inc.   
2     AAP                     Advance Auto Parts, Inc.   
3    AAPL                                   Apple Inc.   
4    ABBV                                  AbbVie Inc.   
5     ABC                AmerisourceBergen Corporation   
6    ABMD                                Abiomed, Inc.   
7     ABT                          Abbott Laboratories   
8     ACN                                Accenture plc   
9    ADBE                                   Adobe Inc.   
10    ADI                         Analog Devices, Inc.   
11    ADM               Archer-Daniels-Midland Company   
12    ADP              Automatic Data Processing, Inc.   
13   ADSK                               Autodesk, Inc.   
14    AEE                           Ameren Corporation   
15    AEP        American Electric Power Company, Inc.   
16    AES                          The AES Corporation   
17    AFL                           Aflac Incorporated   
18    AIG           American International Group, Inc.   
19    AIV  Apartment Investment and Management Company   

                                unofficial_name  
0                          Agilent Technologies  
1                       American Airlines Group  
2                            Advance Auto Parts  
3                                         Apple  
4                                        AbbVie  
5                             AmerisourceBergen  
6                                       Abiomed  
7                           Abbott Laboratories  
8                                     Accenture  
9                                         Adobe  
10                               Analog Devices  
11               Archer-Daniels-Midland Company  
12                    Automatic Data Processing  
13                                     Autodesk  
14                                       Ameren  
15              American Electric Power Company  
16                                      The AES  
17                                        Aflac  
18                 American International Group  
19  Apartment Investment and Management Company

In [9]:
sdate = date(2020, 3, 1)   # start date
edate = date(2020, 10, 1)   # end date

delta = edate - sdate       # as timedelta


date_list= []
for i in range(delta.days + 1):
    day = sdate + timedelta(days=i)
    date_list.append(day)
    #print(day)

#print(date_list)

len(date_list)

215

In [10]:
all_files = []
for date in date_list:
    path = f"results\{date}"
    all_files.append(glob.glob(path + "\*.txt"))

print(all_files)

[['results\\2020-03-01\\Asian stock markets reverse losses on global policy stimulus hopes.txt', 'results\\2020-03-01\\Energy & Precious Metals - Weekly Review and Calendar Ahead.txt', 'results\\2020-03-01\\U.S. officials talk down coronavirus market panic, tout economic strength.txt'], ['results\\2020-03-02\\Coronavirus expected to hurt U.S. earnings harder and longer.txt', 'results\\2020-03-02\\Oil Ends up Nearly 5% on OPEC, Global Rate Cut Hopes.txt', 'results\\2020-03-02\\Stocks - S&P Soars on Bets of Central Banks Stimulus, Slowing China Infections.txt', 'results\\2020-03-02\\Stocks - Wall Street Retreats From Highs After Increase in  U.S. Virus Death Toll.txt', 'results\\2020-03-02\\Stocks - Wall Street Surges at the Close as Financials, Tech Jump.txt', 'results\\2020-03-02\\Stocks – Wall Street Rallies, but Trading Remains Volatile.txt', 'results\\2020-03-02\\U.S. stock short-sellers notch $105 billion week in coronavirus sell-off.txt', 'results\\2020-03-02\\U.S. stocks higher a

In [11]:
text=[]

for file_block in all_files:
    for filename in file_block:
        df = open(filename)
        rows = [row for row in df]
        df.close()
        text.append(rows)
        
print(text)

[['By Tom Westbrook and Swati Pandey SINGAPORE (Reuters) - Asian shares steadied from early losses on Monday as investors placed their hopes on a coordinated global monetary policy response to weather the damaging economic impact of the coronavirus epidemic. Pandemic fears pushed markets off a precipice last week, wiping more than $5 trillion from global share value as stocks cratered to their steepest slump in more than a decade. The sheer scale of losses prompted financial markets to price in policy responses from the U.S. Federal Reserve to the Bank of Japan and the Reserve Bank of Australia. Futures now imply a full 50 basis point cut by the Fed in March  while Australian markets are pricing in a quarter-point cut at the RBA\'s Tuesday meeting. Also helping calm market nerves, Bank of Japan Governor Haruhiko Kuroda said on Monday the central bank would take necessary steps to stabilise financial markets. [ In equities, Chinese shares opened higher with the blue-chip index ( ) up 1.

In [12]:
names=[]

for file_block in all_files:
    for filename in file_block:
        name=filename.split("\\")[2].rstrip(".txt")
        names.append(name)

In [13]:
dates=[]

for file_block in all_files:
    for filename in file_block:
        date=filename.split("\\")[1]
        dates.append(date)
        
print(dates)

['2020-03-01', '2020-03-01', '2020-03-01', '2020-03-02', '2020-03-02', '2020-03-02', '2020-03-02', '2020-03-02', '2020-03-02', '2020-03-02', '2020-03-02', '2020-03-03', '2020-03-03', '2020-03-03', '2020-03-03', '2020-03-03', '2020-03-03', '2020-03-03', '2020-03-03', '2020-03-04', '2020-03-04', '2020-03-04', '2020-03-04', '2020-03-04', '2020-03-05', '2020-03-05', '2020-03-05', '2020-03-05', '2020-03-05', '2020-03-05', '2020-03-06', '2020-03-06', '2020-03-06', '2020-03-06', '2020-03-06', '2020-03-06', '2020-03-06', '2020-03-06', '2020-03-07', '2020-03-08', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-09', '2020-03-10', '2020-03-10', '2020-03-10', '2020-03-10', '2020-03-10', '2020-03-10', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-11', '2020-03-12', '2020-03-12', '2020

In [14]:
dict=[]
for n, d, t in zip(names, dates, text):
    dict_x={"name":n, "date":d, "text":t}
    dict.append(dict_x)

print(dict)

[{'name': 'Asian stock markets reverse losses on global policy stimulus hopes', 'date': '2020-03-01', 'text': ['By Tom Westbrook and Swati Pandey SINGAPORE (Reuters) - Asian shares steadied from early losses on Monday as investors placed their hopes on a coordinated global monetary policy response to weather the damaging economic impact of the coronavirus epidemic. Pandemic fears pushed markets off a precipice last week, wiping more than $5 trillion from global share value as stocks cratered to their steepest slump in more than a decade. The sheer scale of losses prompted financial markets to price in policy responses from the U.S. Federal Reserve to the Bank of Japan and the Reserve Bank of Australia. Futures now imply a full 50 basis point cut by the Fed in March  while Australian markets are pricing in a quarter-point cut at the RBA\'s Tuesday meeting. Also helping calm market nerves, Bank of Japan Governor Haruhiko Kuroda said on Monday the central bank would take necessary steps t

In [15]:
df_news=pd.DataFrame(dict, columns=["name", "date", "text"])

In [28]:
df_news.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1192 entries, 0 to 1191
Columns: 509 entries, name to ZTS
dtypes: float64(4), int64(502), object(3)
memory usage: 4.6+ MB


In [16]:
# Sentiment Analysis
analyzer = SentimentIntensityAnalyzer()

scores = df_news["text"].apply(analyzer.polarity_scores).tolist()

df_scores = pd.DataFrame(scores)
df_news = df_news.join(df_scores, rsuffix='_right')

In [17]:
#creating a matrix of company vs article

company_columns = sp500_names["ticker"]

for col in company_columns:
    df_news[col] = 0

In [18]:
def ngrams(string, n=3):
    string = re.sub(r'[,-./]|\sBD',r'', string)
    ngrams = zip(*[string[i:] for i in range(n)])
    return [''.join(ngram) for ngram in ngrams]

ngrams("Apple")

['App', 'ppl', 'ple']

In [19]:
company_names = sp500_names["unofficial_name"]
article_headlines=df_news["name"]
vectorizer = TfidfVectorizer(min_df=1, analyzer=ngrams)
tf_idf_matrix = vectorizer.fit_transform(article_headlines)
query_vec=vectorizer.transform(company_names)

In [20]:
results = cosine_similarity(tf_idf_matrix,query_vec)
print(results)

[[0.         0.0229667  0.         ... 0.         0.0127679  0.        ]
 [0.04171744 0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.02598726 0.        ]
 ...
 [0.         0.         0.02688635 ... 0.         0.         0.        ]
 [0.         0.01897172 0.         ... 0.         0.02283679 0.        ]
 [0.         0.         0.         ... 0.         0.01686018 0.        ]]


In [31]:
df_names=pd.DataFrame(data=results)

In [32]:
df_names.head(20)

0         1         2    3    4         5    6         7         8    \
0   0.000000  0.022967  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.000000   
1   0.041717  0.000000  0.000000  0.0  0.0  0.029220  0.0  0.000000  0.000000   
2   0.000000  0.000000  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.000000   
3   0.000000  0.000000  0.011509  0.0  0.0  0.000000  0.0  0.000000  0.000000   
4   0.000000  0.000000  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.000000   
5   0.021705  0.000000  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.029057   
6   0.000000  0.000000  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.000000   
7   0.056445  0.004450  0.032224  0.0  0.0  0.032948  0.0  0.000000  0.000000   
8   0.122046  0.004131  0.000000  0.0  0.0  0.000000  0.0  0.025978  0.000000   
9   0.000000  0.000000  0.028948  0.0  0.0  0.000000  0.0  0.000000  0.000000   
10  0.000000  0.019114  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.000000   
11  0.054988  0.003792  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.088641   
12  0.000000  0.059660  0.000000  0.0  0.0  0.000000  0.0  0.026396  0.000000   
13  0.043064  0.000000  0.024584  0.0  0.0  0.000000  0.0  0.000000  0.000000   
14  0.000000  0.000000  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.000000   
15  0.000000  0.000000  0.000000  0.0  0.0  0.000000  0.0  0.075681  0.000000   
16  0.000000  0.003293  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.000000   
17  0.000000  0.018128  0.000000  0.0  0.0  0.000000  0.0  0.000000  0.000000   
18  0.000000  0.004430  0.000000  0.0  0.0  0.040296  0.0  0.035542  0.000000   
19  0.000000  0.003011  0.015911  0.0  0.0  0.047860  0.0  0.024155  0.000000   

    9    ...       492       493  494       495  496       497       498  \
0   0.0  ...  0.000000  0.008991  0.0  0.000000  0.0  0.000000  0.000000   
1   0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.024011  0.000000   
2   0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.007277   
3   0.0  ...  0.000000  0.000000  0.0  0.021837  0.0  0.025227  0.021978   
4   0.0  ...  0.000000  0.009175  0.0  0.033948  0.0  0.021219  0.062057   
5   0.0  ...  0.000000  0.008803  0.0  0.007339  0.0  0.000000  0.005268   
6   0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.013647   
7   0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.010154   
8   0.0  ...  0.000000  0.000000  0.0  0.063265  0.0  0.000000  0.054838   
9   0.0  ...  0.000000  0.056105  0.0  0.000000  0.0  0.000000  0.000000   
10  0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.008366   
11  0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.006611   
12  0.0  ...  0.059034  0.000000  0.0  0.031128  0.0  0.000000  0.022345   
13  0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.000000   
14  0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.000000   
15  0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.008798   
16  0.0  ...  0.000000  0.008695  0.0  0.007249  0.0  0.000000  0.005203   
17  0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.007934   
18  0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.017832   
19  0.0  ...  0.000000  0.000000  0.0  0.000000  0.0  0.000000  0.005249   

         499       500  501  
0   0.000000  0.012768  0.0  
1   0.000000  0.000000  0.0  
2   0.000000  0.025987  0.0  
3   0.000000  0.016676  0.0  
4   0.000000  0.013028  0.0  
5   0.000000  0.129106  0.0  
6   0.000000  0.000000  0.0  
7   0.056385  0.024496  0.0  
8   0.032978  0.050730  0.0  
9   0.000000  0.059067  0.0  
10  0.000000  0.023008  0.0  
11  0.000000  0.008787  0.0  
12  0.000000  0.000000  0.0  
13  0.043018  0.018689  0.0  
14  0.000000  0.010759  0.0  
15  0.000000  0.087019  0.0  
16  0.000000  0.032174  0.0  
17  0.000000  0.021821  0.0  
18  0.000000  0.030382  0.0  
19  0.000000  0.050645  0.0  

[20 rows x 502 columns]

In [33]:
df_names.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1192 entries, 0 to 1191
Columns: 502 entries, 0 to 501
dtypes: float64(502)
memory usage: 4.6 MB


In [34]:
df_names=df_names.rename(columns=sp500_names["ticker"], index=df_news["name"])

In [37]:
df_names.head(500)

A       AAL  \
Asian stock markets reverse losses on global po...  0.000000  0.022967   
Energy & Precious Metals - Weekly Review and Ca...  0.041717  0.000000   
U.S. officials talk down coronavirus market pan...  0.000000  0.000000   
Coronavirus expected to hurt U.S. earnings hard...  0.000000  0.000000   
Oil Ends up Nearly 5% on OPEC, Global Rate Cut ...  0.000000  0.000000   
...                                                      ...       ...   
Stocks - Dow Soars as Vaccine Hopes Trigger Sea...  0.000000  0.060534   
Stocks - Wall Street Jumps at Opening on Reopen...  0.000000  0.020935   
U.S. stocks higher at close of trade; Dow Jones...  0.000000  0.018527   
Home Depot Earnings Miss, Revenue Beats In Q1       0.000000  0.000000   
S&P stumbles as Moderna sinks on report questio...  0.000000  0.003315   

                                                         AAP  AAPL  ABBV  \
Asian stock markets reverse losses on global po...  0.000000   0.0   0.0   
Energy & Precious Metals - Weekly Review and Ca...  0.000000   0.0   0.0   
U.S. officials talk down coronavirus market pan...  0.000000   0.0   0.0   
Coronavirus expected to hurt U.S. earnings hard...  0.011509   0.0   0.0   
Oil Ends up Nearly 5% on OPEC, Global Rate Cut ...  0.000000   0.0   0.0   
...                                                      ...   ...   ...   
Stocks - Dow Soars as Vaccine Hopes Trigger Sea...  0.000000   0.0   0.0   
Stocks - Wall Street Jumps at Opening on Reopen...  0.000000   0.0   0.0   
U.S. stocks higher at close of trade; Dow Jones...  0.000000   0.0   0.0   
Home Depot Earnings Miss, Revenue Beats In Q1       0.000000   0.0   0.0   
S&P stumbles as Moderna sinks on report questio...  0.000000   0.0   0.0   

                                                        ABC      ABMD  ABT  \
Asian stock markets reverse losses on global po...  0.00000  0.000000  0.0   
Energy & Precious Metals - Weekly Review and Ca...  0.02922  0.000000  0.0   
U.S. officials talk down coronavirus market pan...  0.00000  0.000000  0.0   
Coronavirus expected to hurt U.S. earnings hard...  0.00000  0.000000  0.0   
Oil Ends up Nearly 5% on OPEC, Global Rate Cut ...  0.00000  0.000000  0.0   
...                                                     ...       ...  ...   
Stocks - Dow Soars as Vaccine Hopes Trigger Sea...  0.00000  0.000000  0.0   
Stocks - Wall Street Jumps at Opening on Reopen...  0.00000  0.000000  0.0   
U.S. stocks higher at close of trade; Dow Jones...  0.00000  0.000000  0.0   
Home Depot Earnings Miss, Revenue Beats In Q1       0.00000  0.101711  0.0   
S&P stumbles as Moderna sinks on report questio...  0.00000  0.000000  0.0   

                                                    ACN  ADBE  ...  XLNX  \
Asian stock markets reverse losses on global po...  0.0   0.0  ...   0.0   
Energy & Precious Metals - Weekly Review and Ca...  0.0   0.0  ...   0.0   
U.S. officials talk down coronavirus market pan...  0.0   0.0  ...   0.0   
Coronavirus expected to hurt U.S. earnings hard...  0.0   0.0  ...   0.0   
Oil Ends up Nearly 5% on OPEC, Global Rate Cut ...  0.0   0.0  ...   0.0   
...                                                 ...   ...  ...   ...   
Stocks - Dow Soars as Vaccine Hopes Trigger Sea...  0.0   0.0  ...   0.0   
Stocks - Wall Street Jumps at Opening on Reopen...  0.0   0.0  ...   0.0   
U.S. stocks higher at close of trade; Dow Jones...  0.0   0.0  ...   0.0   
Home Depot Earnings Miss, Revenue Beats In Q1       0.0   0.0  ...   0.0   
S&P stumbles as Moderna sinks on report questio...  0.0   0.0  ...   0.0   

                                                         XOM  XRAY       XRX  \
Asian stock markets reverse losses on global po...  0.008991   0.0  0.000000   
Energy & Precious Metals - Weekly Review and Ca...  0.000000   0.0  0.000000   
U.S. officials talk down coronavirus market pan...  0.000000   0.0  0.000000   
Coronavirus expected to hurt U.S. earnings hard...  0.000000   0.0  0.021837   
Oil End

In [38]:
df_names.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1192 entries, Asian stock markets reverse losses on global policy stimulus hopes to Wall Street Opens Higher on Stimulus Hopes; Dow up 220 Points
Columns: 502 entries, A to ZTS
dtypes: float64(502)
memory usage: 4.6+ MB


In [39]:
df_names.tail(50)

A       AAL  \
Nike Jumps on Blowout Q1 Earnings Amid Direct t...  0.000000  0.028004   
U.S. Futures Edge Higher Ahead of Powell Testimony  0.017603  0.004398   
U.S. stocks higher at close of trade; Dow Jones...  0.000000  0.018918   
Wall Street closes higher on Amazon boost, desp...  0.029554  0.038630   
Wall Street Opens Higher in Cautious Bounce; Te...  0.014421  0.000000   
'Active' fund managers beaten by benchmarks dur...  0.000000  0.000000   
Cintas Earnings, Revenue Beat in Q1                 0.000000  0.000000   
Dow Futures Rise 225 Pts; Nike Set to Shine         0.000000  0.025417   
Dow Sheds 525 Points as Tech Rout Rattles Bulls     0.051058  0.004025   
Dow Slumps as Tech Turns Ugly                       0.072476  0.000000   
European Stocks Seen Higher Ahead of Key PMI Se...  0.075495  0.020639   
U.S. stocks lower at close of trade; Dow Jones ...  0.000000  0.018360   
Wall Street closes lower on fears of a slowing ...  0.000000  0.004450   
Wall Street Turns Lower on Downbeat Fed Comment...  0.056711  0.000000   
Accenture Earnings Miss, Revenue Inline In Q4       0.028961  0.047060   
Dow Ends Slightly Higher as Wild Swings Weigh       0.000000  0.000000   
Dow in Choppy Trade as Tech Strength Cools          0.057285  0.000000   
European Stocks Seen Lower; Global Recovery Hop...  0.000000  0.026978   
Global shares slide, dollar up as hopes of econ...  0.000000  0.007058   
U.S. Futures Edge Lower; Powell in Spotligh         0.000000  0.004324   
U.S. stocks higher at close of trade; Dow Jones...  0.000000  0.019089   
Wall Street closes up on tech rally despite mix...  0.014621  0.003488   
Wall Street Falls Again at Open on Economy Fear...  0.000000  0.000000   
Dow Higher on Tech Strength as Yo-Yo Trading Co...  0.051736  0.000000   
European Stocks Largely Weaken; Covid-19 Resurg...  0.000000  0.019944   
European Stocks Seen Higher; US Stimulus Talk H...  0.000000  0.024254   
Nasdaq Snaps 3-Week Losing Streak as Apple Rest...  0.045942  0.003622   
Tech ETF outflows send a wake-up call after siz...  0.027413  0.017627   
U.S. stocks higher at close of trade; Dow Jones...  0.000000  0.018831   
Wall Street Drifts Lower Again as Durable Goods...  0.000000  0.000000   
Dow Jumps as Bulls Up Bets on Financials, Indus...  0.000000  0.000000   
Dow Racks Up 410 Point Gain as Traders Bid Up B...  0.076272  0.000000   
Japan's little-known Nikkei 500 hits record hig...  0.000000  0.000000   
Wall Street jumps, financials take the lead         0.000000  0.000000   
Wall Street Opens Higher as Rebound Continues; ...  0.000000  0.000000   
Dow Ends Lower as Bulls Meet Resistance From En...  0.000000  0.000000   
Dow Off Lows but Remains in Red as Weakness in ...  0.000000  0.010722   
Micron Rolls Out Soft Guidance, But Earnings Be...  0.000000  0.000000   
Wall Street Opens Flat Ahead of 1st Election De...  0.000000  0.000000   
Yen safety status at risk from pandemic-era glo...  0.000000  0.003001   
Chaotic U.S. election debate fuels investors' f...  0.000000  0.000000   
Dollar outshining gold, beating yen in battle o...  0.000000  0.000000   
Dow Cuts Gains on Stimulus Uncertainty as Mnuch...  0.000000  0.023524   
Dow Shrugs Off Stimulus Uncertainty to Close Hi...  0.000000  0.000000   
Dow Cuts Gains on Stimulus Stalemate; Tech Cont...  0.052504  0.032996   
Dow Cuts Gains on Stimulus Uncertainty as Mnuch...  0.000000  0.023524   
Dow Ekes Out Gain as Pelosi Rips White House Of...  0.000000  0.020536   
Dow Shrugs Off Stimulus Uncertainty to Close Hi...  0.000000  0.000000   
U.S. stocks higher at close of trade; Dow Jones...  0.000000  0.018972   
Wall Street Opens Higher on Stimulus Hopes; Dow...  0.000000  0.000000   

                                                         AAP     AAPL  ABBV  \
Nike Jumps on Blowout Q1 Earnings Amid Direct t...  0.010942  0.00000   0.0   
U.S. Futures Edge Higher Ahead of Powell Testimony  0.000000  0.00000   0.0   
U.S. stocks higher at close of trade; Dow Jones